# Hotel Booking Demand & Cancellation Analytics

## Data Ingestion Constraints & Chosen Approach

- **DBFS & local FS writes blocked**  
  Community Edition disallows shell writes to `dbfs:/…` and direct writes to the driver’s `/tmp` filesystem, so we cannot persist files there.

- **Kaggle API impractical**  
  Installing and authenticating the Kaggle CLI in this environment requires on-disk credentials and network installations that fail under these restrictions.

- **HTTPS ingestion limitations**  
  Spark’s native HTTP-FS support is restricted in Community Edition, so commands like `spark.read.csv("https://…")` either error out or return empty data.

- **Final solution: GitHub → pandas → Spark**  
  We commit the raw `hotel_bookings.csv` to our public GitHub repo and load it in-memory via `pandas.read_csv()` over HTTPS, then convert to a Spark DataFrame. This keeps the pipeline reproducible, code-only, and free of filesystem/HTTP-FS limitations.  


In [0]:
import pandas as pd

# 1. Load via pandas from the raw GitHub URL
url = "https://raw.githubusercontent.com/anmolkalra/airbnb-revenue-optimizer/main/hotel_bookings.csv"
pdf = pd.read_csv(url)

# 2. Lift into Spark
bookings_df = spark.createDataFrame(pdf)
display(bookings_df.limit(5))

# 3. Stage as a Delta table
bookings_df.write \
  .format("delta") \
  .mode("overwrite") \
  .saveAsTable("stg_hotel_bookings")


hotel is_canceled lead_time arrival_date_year arrival_date_month arrival_date_week_number arrival_date_day_of_month stays_in_weekend_nights stays_in_week_nights adults children babies meal country market_segment distribution_channel is_repeated_guest previous_cancellations previous_bookings_not_canceled reserved_room_type assigned_room_type booking_changes deposit_type agent company days_in_waiting_list customer_type adr required_car_parking_spaces total_of_special_requests reservation_status reservation_status_date Resort Hotel 0 342 2015 July 27 1 0 0 2 0.0 0 BB PRT Direct Direct 0 0 0 C C 3 No Deposit null null 0 Transient 0.0 0 0 Check-Out 2015-07-01 Resort Hotel 0 737 2015 July 27 1 0 0 2 0.0 0 BB PRT Direct Direct 0 0 0 C C 4 No Deposit null null 0 Transient 0.0 0 0 Check-Out 2015-07-01 Resort Hotel 0 7 2015 July 27 1 0 1 1 0.0 0 BB GBR Direct Direct 0 0 0 A C 0 No Deposit null null 0 Transient 75.0 0 0 Check-Out 2015-07-02 Resort Hotel 0 13 2015 July 27 1 0 1 1 0.0 0 BB GBR Corporate Corporate 0 0 0 A A 0 No Deposit 304.0 null 0 Transient 75.0 0 0 Check-Out 2015-07-02 Resort Hotel 0 14 2015 July 27 1 0 2 2 0.0 0 BB GBR Online TA TA/TO 0 0 0 A A 0 No Deposit 240.0 null 0 Transient 98.0 0 1 Check-Out 2015-07-03

In [0]:
%sql
SELECT
  COUNT(*)                                AS total_rows,
  SUM(CASE WHEN arrival_date_year   IS NULL THEN 1 ELSE 0 END) AS missing_year,
  SUM(CASE WHEN arrival_date_month  IS NULL THEN 1 ELSE 0 END) AS missing_month,
  SUM(CASE WHEN arrival_date_day_of_month IS NULL THEN 1 ELSE 0 END) AS missing_day,
  SUM(CASE WHEN lead_time < 0        THEN 1 ELSE 0 END)        AS neg_lead_time,
  SUM(CASE WHEN adr <= 0             THEN 1 ELSE 0 END)        AS nonpos_adr
FROM stg_hotel_bookings;

total_rows missing_year missing_month missing_day neg_lead_time nonpos_adr 119390 0 0 0 0 1960

In [0]:
%sql
-- Clean staging view with robust date parsing and a surrogate key
CREATE OR REPLACE TEMP VIEW vw_bookings_clean AS
SELECT
  -- 1) Surrogate booking key
  ROW_NUMBER() OVER (
    ORDER BY
      arrival_date_year,
      arrival_date_month,
      arrival_date_day_of_month,
      lead_time
  ) AS booking_key,

  -- 2) Parse arrival_date using TRY_TO_DATE and explicit month→MM mapping
  TO_DATE(
    CONCAT(
      arrival_date_year, '-',
      CASE arrival_date_month
        WHEN 'January'   THEN '01'
        WHEN 'February'  THEN '02'
        WHEN 'March'     THEN '03'
        WHEN 'April'     THEN '04'
        WHEN 'May'       THEN '05'
        WHEN 'June'      THEN '06'
        WHEN 'July'      THEN '07'
        WHEN 'August'    THEN '08'
        WHEN 'September' THEN '09'
        WHEN 'October'   THEN '10'
        WHEN 'November'  THEN '11'
        WHEN 'December'  THEN '12'
        ELSE '00'           -- fallback
      END, '-',
      LPAD(CAST(arrival_date_day_of_month AS STRING), 2, '0')
    ),
    'yyyy-MM-dd'
  ) AS arrival_date,

  -- 3) All other cleaned fields
  hotel,
  is_canceled,
  lead_time,
  stays_in_week_nights,
  stays_in_weekend_nights,
  adults,
  children,
  babies,
  adr,
  previous_cancellations,
  previous_bookings_not_canceled,
  customer_type,
  is_repeated_guest,
  market_segment

FROM stg_hotel_bookings
WHERE 
  -- filter out clearly invalid rows
  arrival_date_year            IS NOT NULL
  AND arrival_date_month       IS NOT NULL
  AND arrival_date_day_of_month IS NOT NULL
  AND lead_time >= 0
  AND adr > 0;


In [0]:
%sql
select * from vw_bookings_clean

booking_key arrival_date hotel is_canceled lead_time stays_in_week_nights stays_in_weekend_nights adults children babies adr previous_cancellations previous_bookings_not_canceled customer_type is_repeated_guest market_segment 1 2015-08-01 Resort Hotel 0 0 1 0 2 0.0 0 200.0 0 1 Transient 0 Direct 2 2015-08-01 City Hotel 0 0 1 0 2 0.0 0 75.0 0 0 Transient 0 Direct 3 2015-08-01 Resort Hotel 0 0 5 2 2 1.0 0 120.6 0 0 Transient 0 Online TA 4 2015-08-01 Resort Hotel 0 0 1 0 2 0.0 0 132.44 0 0 Transient 0 Online TA 5 2015-08-01 Resort Hotel 0 1 1 0 2 0.0 0 211.0 0 0 Transient 0 Online TA 6 2015-08-01 Resort Hotel 0 1 1 2 2 2.0 0 252.0 0 0 Transient 0 Online TA 7 2015-08-01 Resort Hotel 0 1 1 1 2 0.0 0 162.5 0 0 Transient 0 Online TA 8 2015-08-01 City Hotel 1 2 1 2 2 0.0 0 94.5 0 0 Transient-Party 0 Offline TA/TO 9 2015-08-01 City Hotel 1 2 1 2 2 0.0 0 94.5 0 0 Transient-Party 0 Offline TA/TO 10 2015-08-01 City Hotel 1 2 1 2 2 0.0 0 94.5 0 0 Transient-Party 0 Offline TA/TO 11 2015-08-01 Resort Hotel 1 3 3 2 2 2.0 0 237.0 0 0 Transient 0 Direct 12 2015-08-01 Resort Hotel 0 3 5 2 2 0.0 0 188.29 0 0 Transient 0 Online TA 13 2015-08-01 Resort Hotel 0 3 5 2 2 2.0 0 163.33 0 0 Transient 0 Online TA 14 2015-08-01 City Hotel 0 4 1 2 1 0.0 0 36.25 0 0 Transient-Party 0 Offline TA/TO 15 2015-08-01 Resort Hotel 0 5 3 2 2 1.0 0 165.32 0 0 Transient 0 Online TA 16 2015-08-01 Resort Hotel 1 9 1 0 2 0.0 0 211.0 0 0 Transient 0 Online TA 17 2015-08-01 Resort Hotel 0 10 5 2 2 0.0 0 219.9 0 0 Transient 0 Direct 18 2015-08-01 Resort Hotel 1 10 1 0 2 0.0 0 202.0 0 0 Transient-Party 0 Direct 19 2015-08-01 Resort Hotel 1 10 1 0 2 0.0 0 202.0 0 0 Transient-Party 0 Direct 20 2015-08-01 Resort Hotel 1 10 1 0 2 0.0 0 252.0 0 0 Transient-Party 0 Direct 21 2015-08-01 Resort Hotel 0 11 10 4 1 0.0 0 172.0 0 0 Transient 0 Offline TA/TO 22 2015-08-01 Resort Hotel 0 22 1 1 2 0.0 0 134.0 0 0 Transient 0 Direct 23 2015-08-01 Resort Hotel 1 24 1 0 2 2.0 0 233.0 0 0 Transient 0 Online TA 24 2015-08-01 Resort Hotel 0 32 6 2 2 0.0 0 176.75 0 0 Transient 0 Online TA 25 2015-08-01 Resort Hotel 0 44 1 1 2 0.0 0 154.0 0 0 Transient 0 Online TA 26 2015-08-01 Resort Hotel 1 53 6 3 2 0.0 0 210.78 0 0 Transient 0 Online TA 27 2015-08-01 Resort Hotel 1 57 10 4 2 2.0 0 135.53 0 0 Transient 0 Online TA 28 2015-08-01 Resort Hotel 0 64 1 1 2 0.0 0 154.0 0 0 Transient 0 Online TA 29 2015-08-01 Resort Hotel 0 66 6 2 2 0.0 0 193.13 0 0 Transient 0 Online TA 30 2015-08-01 Resort Hotel 0 67 6 4 2 0.0 0 191.7 0 0 Transient 0 Online TA 31 2015-08-01 Resort Hotel 0 67 6 2 2 0.0 0 193.13 0 0 Transient 0 Online TA 32 2015-08-01 Resort Hotel 0 67 6 2 2 0.0 0 193.13 0 0 Transient 0 Online TA 33 2015-08-01 Resort Hotel 0 67 6 4 2 0.0 0 208.2 0 0 Transient 0 Online TA 34 2015-08-01 Resort Hotel 0 70 5 2 2 0.0 0 187.14 0 0 Transient 0 Direct 35 2015-08-01 Resort Hotel 1 74 5 2 2 2.0 0 177.14 0 0 Transient 0 Direct 36 2015-08-01 Resort Hotel 0 77 2 2 1 0.0 0 201.5 0 0 Transient 0 Offline TA/TO 37 2015-08-01 Resort Hotel 1 77 5 2 2 0.0 0 194.14 0 0 Transient 0 Online TA 38 2015-08-01 Resort Hotel 1 77 6 4 2 1.0 0 174.7 0 0 Transient 0 Online TA 39 2015-08-01 Resort Hotel 0 78 1 1 2 0.0 0 150.0 0 0 Transient 0 Direct 40 2015-08-01 Resort Hotel 0 79 5 2 3 0.0 0 185.0 0 0 Transient 0 Direct 41 2015-08-01 Resort Hotel 0 79 2 2 2 0.0 0 149.0 0 0 Transient 0 Offline TA/TO 42 2015-08-01 Resort Hotel 1 80 1 0 2 0.0 0 134.0 0 0 Transient 0 Online TA 43 2015-08-01 Resort Hotel 1 80 6 4 2 2.0 0 169.0 0 0 Transient 0 Online TA 44 2015-08-01 Resort Hotel 0 82 2 2 2 1.0 0 143.5 0 0 Transient 0 Online TA 45 2015-08-01 Resort Hotel 0 82 5 2 2 0.0 0 162.14 0 0 Transient 0 Online TA 46 2015-08-01 Resort Hotel 1 82 5 2 2 2.0 0 222.14 0 0 Transient 0 Online TA 47 2015-08-01 Resort Hotel 1 84 1 2 2 0.0 0 118.06 0 0 Transient-Party 0 Offline TA/TO 48 2015-08-01 Resort Hotel 1 84 1 2 2 0.0 0 118.06 0 0 Transient-Party 0 Offline TA/TO 49 2015-08-01 Resort Hotel 1 89 1 0 2 0.0 0 154.0 0 0 Transient 0 Direct 50 2015-08-01 Resor

#Dim_date table 

In [0]:
%pip install --quiet holidays
# 1. Generate a full calendar for your booking window
import pandas as pd
import holidays
from pyspark.sql import SparkSession

spark = SparkSession.builder.getOrCreate()

# a) date range matching your data: July 1 2015 → Aug 31 2017
dates = pd.date_range("2015-07-01", "2017-08-31", freq="D")
df_dates = pd.DataFrame({"date": dates})

# b) derive keys & attributes
df_dates["date_key"]     = df_dates["date"].dt.strftime("%Y%m%d").astype(int)
df_dates["year"]         = df_dates["date"].dt.year
df_dates["quarter"]      = df_dates["date"].dt.quarter
df_dates["month"]        = df_dates["date"].dt.month
df_dates["day_of_week"]  = df_dates["date"].dt.dayofweek + 1
df_dates["is_weekend"]   = df_dates["day_of_week"].isin([6,7]).astype(int)

# c) flag holidays (e.g. Portugal calendar)
hcal = holidays.CountryHoliday("PT", years=[2015,2016,2017])
df_dates["is_holiday"]   = df_dates["date"].isin(hcal).astype(int)

# 2. Push into Spark and write as a Delta table
dim_date = spark.createDataFrame(df_dates)
dim_date.write \
        .format("delta") \
        .mode("overwrite") \
        .saveAsTable("dim_date")


Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%sql
select * from dim_date

date date_key year quarter month day_of_week is_weekend is_holiday 2015-07-01T00:00:00.000Z 20150701 2015 3 7 3 0 0 2015-07-02T00:00:00.000Z 20150702 2015 3 7 4 0 0 2015-07-03T00:00:00.000Z 20150703 2015 3 7 5 0 0 2015-07-04T00:00:00.000Z 20150704 2015 3 7 6 1 0 2015-07-05T00:00:00.000Z 20150705 2015 3 7 7 1 0 2015-07-06T00:00:00.000Z 20150706 2015 3 7 1 0 0 2015-07-07T00:00:00.000Z 20150707 2015 3 7 2 0 0 2015-07-08T00:00:00.000Z 20150708 2015 3 7 3 0 0 2015-07-09T00:00:00.000Z 20150709 2015 3 7 4 0 0 2015-07-10T00:00:00.000Z 20150710 2015 3 7 5 0 0 2015-07-11T00:00:00.000Z 20150711 2015 3 7 6 1 0 2015-07-12T00:00:00.000Z 20150712 2015 3 7 7 1 0 2015-07-13T00:00:00.000Z 20150713 2015 3 7 1 0 0 2015-07-14T00:00:00.000Z 20150714 2015 3 7 2 0 0 2015-07-15T00:00:00.000Z 20150715 2015 3 7 3 0 0 2015-07-16T00:00:00.000Z 20150716 2015 3 7 4 0 0 2015-07-17T00:00:00.000Z 20150717 2015 3 7 5 0 0 2015-07-18T00:00:00.000Z 20150718 2015 3 7 6 1 0 2015-07-19T00:00:00.000Z 20150719 2015 3 7 7 1 0 2015-07-20T00:00:00.000Z 20150720 2015 3 7 1 0 0 2015-07-21T00:00:00.000Z 20150721 2015 3 7 2 0 0 2015-07-22T00:00:00.000Z 20150722 2015 3 7 3 0 0 2015-07-23T00:00:00.000Z 20150723 2015 3 7 4 0 0 2015-07-24T00:00:00.000Z 20150724 2015 3 7 5 0 0 2015-07-25T00:00:00.000Z 20150725 2015 3 7 6 1 0 2015-07-26T00:00:00.000Z 20150726 2015 3 7 7 1 0 2015-07-27T00:00:00.000Z 20150727 2015 3 7 1 0 0 2015-07-28T00:00:00.000Z 20150728 2015 3 7 2 0 0 2015-07-29T00:00:00.000Z 20150729 2015 3 7 3 0 0 2015-07-30T00:00:00.000Z 20150730 2015 3 7 4 0 0 2015-07-31T00:00:00.000Z 20150731 2015 3 7 5 0 0 2015-08-01T00:00:00.000Z 20150801 2015 3 8 6 1 0 2015-08-02T00:00:00.000Z 20150802 2015 3 8 7 1 0 2015-08-03T00:00:00.000Z 20150803 2015 3 8 1 0 0 2015-08-04T00:00:00.000Z 20150804 2015 3 8 2 0 0 2015-08-05T00:00:00.000Z 20150805 2015 3 8 3 0 0 2015-08-06T00:00:00.000Z 20150806 2015 3 8 4 0 0 2015-08-07T00:00:00.000Z 20150807 2015 3 8 5 0 0 2015-08-08T00:00:00.000Z 20150808 2015 3 8 6 1 0 2015-08-09T00:00:00.000Z 20150809 2015 3 8 7 1 0 2015-08-10T00:00:00.000Z 20150810 2015 3 8 1 0 0 2015-08-11T00:00:00.000Z 20150811 2015 3 8 2 0 0 2015-08-12T00:00:00.000Z 20150812 2015 3 8 3 0 0 2015-08-13T00:00:00.000Z 20150813 2015 3 8 4 0 0 2015-08-14T00:00:00.000Z 20150814 2015 3 8 5 0 0 2015-08-15T00:00:00.000Z 20150815 2015 3 8 6 1 1 2015-08-16T00:00:00.000Z 20150816 2015 3 8 7 1 0 2015-08-17T00:00:00.000Z 20150817 2015 3 8 1 0 0 2015-08-18T00:00:00.000Z 20150818 2015 3 8 2 0 0 2015-08-19T00:00:00.000Z 20150819 2015 3 8 3 0 0 2015-08-20T00:00:00.000Z 20150820 2015 3 8 4 0 0 2015-08-21T00:00:00.000Z 20150821 2015 3 8 5 0 0 2015-08-22T00:00:00.000Z 20150822 2015 3 8 6 1 0 2015-08-23T00:00:00.000Z 20150823 2015 3 8 7 1 0 2015-08-24T00:00:00.000Z 20150824 2015 3 8 1 0 0 2015-08-25T00:00:00.000Z 20150825 2015 3 8 2 0 0 2015-08-26T00:00:00.000Z 20150826 2015 3 8 3 0 0 2015-08-27T00:00:00.000Z 20150827 2015 3 8 4 0 0 2015-08-28T00:00:00.000Z 20150828 2015 3 8 5 0 0 2015-08-29T00:00:00.000Z 20150829 2015 3 8 6 1 0 2015-08-30T00:00:00.000Z 20150830 2015 3 8 7 1 0 2015-08-31T00:00:00.000Z 20150831 2015 3 8 1 0 0 2015-09-01T00:00:00.000Z 20150901 2015 3 9 2 0 0 2015-09-02T00:00:00.000Z 20150902 2015 3 9 3 0 0 2015-09-03T00:00:00.000Z 20150903 2015 3 9 4 0 0 2015-09-04T00:00:00.000Z 20150904 2015 3 9 5 0 0 2015-09-05T00:00:00.000Z 20150905 2015 3 9 6 1 0 2015-09-06T00:00:00.000Z 20150906 2015 3 9 7 1 0 2015-09-07T00:00:00.000Z 20150907 2015 3 9 1 0 0 2015-09-08T00:00:00.000Z 20150908 2015 3 9 2 0 0 2015-09-09T00:00:00.000Z 20150909 2015 3 9 3 0 0 2015-09-10T00:00:00.000Z 20150910 2015 3 9 4 0 0 2015-09-11T00:00:00.000Z 20150911 2015 3 9 5 0 0 2015-09-12T00:00:00.000Z 20150912 2015 3 9 6 1 0 2015-09-13T00:00:00.000Z 20150913 2015 3 9 7 1 0 2015-09-14T00:00:00.000Z 20150914 2015 3 9 1 0 0 2015-09-15T00:00:00.000Z 20150915 2015 3 9 2 0 0 2015-09-16T00:00:00.000Z 20150916 2015 3 9 3 0 0 2015-09-17T00:00:00.000Z 20150917 2015 3 9 4 0 0 2015-09-18T00:00:00.000Z 20150918 2015 3 9 5 0 0 2015-09-19T00

#Every other dimensional table

In [0]:
%sql
-- dim_hotel
CREATE OR REPLACE TABLE dim_hotel AS
SELECT
  ROW_NUMBER() OVER (ORDER BY hotel) AS hotel_id,
  hotel AS hotel_type
FROM (SELECT DISTINCT hotel FROM vw_bookings_clean);

-- dim_customer
CREATE OR REPLACE TABLE dim_customer AS
SELECT
  ROW_NUMBER() OVER (ORDER BY is_repeated_guest, customer_type) AS customer_type_id,
  is_repeated_guest,
  customer_type
FROM (
  SELECT DISTINCT is_repeated_guest, customer_type 
  FROM vw_bookings_clean
);

-- dim_market
CREATE OR REPLACE TABLE dim_market AS
SELECT
  ROW_NUMBER() OVER (ORDER BY market_segment) AS market_id,
  market_segment
FROM (
  SELECT DISTINCT market_segment 
  FROM vw_bookings_clean
);


num_affected_rows num_inserted_rows

# Facts table

In [0]:
%sql
CREATE OR REPLACE TABLE fact_booking AS
SELECT
  hb.booking_key,
  d.date_key,
  h.hotel_id,
  c.customer_type_id,
  m.market_id,
  hb.is_canceled,
  hb.lead_time,
  hb.stays_in_week_nights,
  hb.stays_in_weekend_nights,
  hb.adults,
  hb.children,
  hb.babies,
  hb.adr,
  hb.previous_cancellations,
  hb.previous_bookings_not_canceled
FROM vw_bookings_clean hb
JOIN dim_date     d ON hb.arrival_date = d.date
JOIN dim_hotel    h ON hb.hotel = h.hotel_type
JOIN dim_customer c ON hb.is_repeated_guest = c.is_repeated_guest
                    AND hb.customer_type = c.customer_type
JOIN dim_market   m ON hb.market_segment = m.market_segment;


num_affected_rows num_inserted_rows

In [0]:
%sql
select * from fact_booking

booking_key date_key hotel_id customer_type_id market_id is_canceled lead_time stays_in_week_nights stays_in_weekend_nights adults children babies adr previous_cancellations previous_bookings_not_canceled 1 20150801 2 3 7 0 0 1 0 2 0.0 0 132.44 0 0 2 20150801 2 3 7 0 0 5 2 2 1.0 0 120.6 0 0 3 20150801 1 3 4 0 0 1 0 2 0.0 0 75.0 0 0 4 20150801 2 3 4 0 0 1 0 2 0.0 0 200.0 0 1 5 20150801 2 3 7 0 1 1 1 2 0.0 0 162.5 0 0 6 20150801 2 3 7 0 1 1 2 2 2.0 0 252.0 0 0 7 20150801 2 3 7 0 1 1 0 2 0.0 0 211.0 0 0 8 20150801 1 4 6 1 2 1 2 2 0.0 0 94.5 0 0 9 20150801 1 4 6 1 2 1 2 2 0.0 0 94.5 0 0 10 20150801 1 4 6 1 2 1 2 2 0.0 0 94.5 0 0 11 20150801 2 3 7 0 3 5 2 2 2.0 0 163.33 0 0 12 20150801 2 3 4 1 3 3 2 2 2.0 0 237.0 0 0 13 20150801 2 3 7 0 3 5 2 2 0.0 0 188.29 0 0 14 20150801 1 4 6 0 4 1 2 1 0.0 0 36.25 0 0 15 20150801 2 3 7 0 5 3 2 2 1.0 0 165.32 0 0 16 20150801 2 3 7 1 9 1 0 2 0.0 0 211.0 0 0 17 20150801 2 3 4 0 10 5 2 2 0.0 0 219.9 0 0 18 20150801 2 4 4 1 10 1 0 2 0.0 0 202.0 0 0 19 20150801 2 4 4 1 10 1 0 2 0.0 0 202.0 0 0 20 20150801 2 4 4 1 10 1 0 2 0.0 0 252.0 0 0 21 20150801 2 3 6 0 11 10 4 1 0.0 0 172.0 0 0 22 20150801 2 3 4 0 22 1 1 2 0.0 0 134.0 0 0 23 20150801 2 3 7 1 24 1 0 2 2.0 0 233.0 0 0 24 20150801 2 3 7 0 32 6 2 2 0.0 0 176.75 0 0 25 20150801 2 3 7 0 44 1 1 2 0.0 0 154.0 0 0 26 20150801 2 3 7 1 53 6 3 2 0.0 0 210.78 0 0 27 20150801 2 3 7 1 57 10 4 2 2.0 0 135.53 0 0 28 20150801 2 3 7 0 64 1 1 2 0.0 0 154.0 0 0 29 20150801 2 3 7 0 66 6 2 2 0.0 0 193.13 0 0 30 20150801 2 3 7 0 67 6 2 2 0.0 0 193.13 0 0 31 20150801 2 3 7 0 67 6 2 2 0.0 0 193.13 0 0 32 20150801 2 3 7 0 67 6 4 2 0.0 0 191.7 0 0 33 20150801 2 3 7 0 67 6 4 2 0.0 0 208.2 0 0 34 20150801 2 3 4 0 70 5 2 2 0.0 0 187.14 0 0 35 20150801 2 3 4 1 74 5 2 2 2.0 0 177.14 0 0 36 20150801 2 3 6 0 77 2 2 1 0.0 0 201.5 0 0 37 20150801 2 3 7 1 77 5 2 2 0.0 0 194.14 0 0 38 20150801 2 3 7 1 77 6 4 2 1.0 0 174.7 0 0 39 20150801 2 3 4 0 78 1 1 2 0.0 0 150.0 0 0 40 20150801 2 3 6 0 79 2 2 2 0.0 0 149.0 0 0 41 20150801 2 3 4 0 79 5 2 3 0.0 0 185.0 0 0 42 20150801 2 3 7 1 80 1 0 2 0.0 0 134.0 0 0 43 20150801 2 3 7 1 80 6 4 2 2.0 0 169.0 0 0 44 20150801 2 3 7 0 82 2 2 2 1.0 0 143.5 0 0 45 20150801 2 3 7 0 82 5 2 2 0.0 0 162.14 0 0 46 20150801 2 3 7 1 82 5 2 2 2.0 0 222.14 0 0 47 20150801 2 4 6 1 84 1 2 2 0.0 0 118.06 0 0 48 20150801 2 4 6 1 84 1 2 2 0.0 0 118.06 0 0 49 20150801 2 3 4 1 89 1 0 2 0.0 0 154.0 0 0 50 20150801 2 3 7 1 91 5 2 2 0.0 0 127.82 0 0 51 20150801 2 3 7 1 91 5 2 2 1.0 0 144.53 0 0 52 20150801 1 3 7 0 94 4 2 2 0.0 0 76.5 0 0 53 20150801 2 3 4 0 103 4 2 2 0.0 0 179.0 0 0 54 20150801 2 3 4 0 103 9 4 2 1.0 0 297.5 0 0 55 20150801 2 3 4 0 105 6 3 1 0.0 0 140.0 0 0 56 20150801 2 3 4 0 113 42 18 1 0.0 0 110.5 0 0 57 20150801 1 4 6 0 117 1 2 2 0.0 0 89.75 0 0 58 20150801 1 4 6 0 117 1 2 1 0.0 0 72.5 0 0 59 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 60 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 61 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 62 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 63 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 64 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 65 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 66 20150801 1 4 6 0 117 1 2 3 0.0 0 138.5 0 0 67 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 68 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 69 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 70 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 71 20150801 1 4 6 0 117 1 2 1 0.0 0 72.5 0 0 72 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 73 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 74 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 75 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 76 20150801 1 4 6 0 117 1 2 1 1.0 0 80.75 0 0 77 20150801 1 4 6 0 117 1 2 1 0.0 0 72.5 0 0 78 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 79 20150801 1 4 6 1 117 1 2 2 0.0 0 94.5 0 0 80 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 81 20150801 1 4 6 0 117 1 2 2 0.0 0 94.5 0 0 82 20150801 2 3 7 0 124 5 2 2 0.0 0 120.6 0 0 83 20150801 2 3 7 1 124 4 2 2 0.0 0 120.6 0 0 84 20150801 2 3 4 0 129 6 3 2 0.0 0 125.9 0 0 85 20150801 

In [0]:
%sql
CREATE OR REPLACE TABLE fact_booking_partitioned
USING DELTA
PARTITIONED BY (year, hotel_id) AS
SELECT
  f.*,
  d.year
FROM fact_booking f
JOIN dim_date d
  ON f.date_key = d.date_key;

num_affected_rows num_inserted_rows

# Visualization

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_cancel_rate AS
SELECT
  d.year,
  d.month,
  h.hotel_type,
  AVG(f.is_canceled) * 100 AS cancel_rate_pct
FROM fact_booking_partitioned f
JOIN dim_date d      ON f.date_key = d.date_key
JOIN dim_hotel h     ON f.hotel_id = h.hotel_id
GROUP BY d.year, d.month, h.hotel_type
ORDER BY d.year, d.month, h.hotel_type;

In [0]:
# Cancellation rate by month & hotel
cancel_df = spark.table("vw_cancel_rate")
display(cancel_df)

year month hotel_type cancel_rate_pct 2015 7 City Hotel 68.952802359882 2015 7 Resort Hotel 23.49042709867452 2015 8 City Hotel 51.060291060291064 2015 8 Resort Hotel 26.34989200863931 2015 9 City Hotel 44.47986090988119 2015 9 Resort Hotel 34.59563543003851 2015 10 City Hotel 39.4856278366112 2015 10 Resort Hotel 26.33311389071758 2015 11 City Hotel 24.72939217318901 2015 11 Resort Hotel 17.148182665424045 2015 12 City Hotel 42.21233312142403 2015 12 Resort Hotel 24.631751227495908 2016 1 City Hotel 32.605421686746986 2016 1 Resort Hotel 13.684210526315791 2016 2 City Hotel 39.544869042507514 2016 2 Resort Hotel 27.16297786720322 2016 3 City Hotel 36.71770972037284 2016 3 Resort Hotel 20.979827089337174 2016 4 City Hotel 43.53509519749929 2016 4 Resort Hotel 28.461959496442258 2016 5 City Hotel 39.73399833748961 2016 5 Resort Hotel 26.905574516496017 2016 6 City Hotel 44.18425115800309 2016 6 Resort Hotel 27.96420581655481 2016 7 City Hotel 33.53856124432923 2016 7 Resort Hotel 31.94933145672062 2016 8 City Hotel 37.134328358208954 2016 8 Resort Hotel 34.550898203592816 2016 9 City Hotel 40.850952753850166 2016 9 Resort Hotel 29.9801455989411 2016 10 City Hotel 46.70831331090822 2016 10 Resort Hotel 28.821410190427176 2016 11 City Hotel 44.241435562805876 2016 11 Resort Hotel 20.967741935483872 2016 12 City Hotel 43.7782340862423 2016 12 Resort Hotel 24.34259954921112 2017 1 City Hotel 44.51557831839522 2017 1 Resort Hotel 15.84313725490196 2017 2 City Hotel 37.90259230164965 2017 2 Resort Hotel 24.758842443729904 2017 3 City Hotel 37.949479940564636 2017 3 Resort Hotel 25.56929082628497 2017 4 City Hotel 49.34396706971958 2017 4 Resort Hotel 31.046511627906977 2017 5 City Hotel 48.95833333333333 2017 5 Resort Hotel 31.351039260969976 2017 6 City Hotel 45.903307888040715 2017 6 Resort Hotel 37.725631768953065 2017 7 City Hotel 37.404580152671755 2017 7 Resort Hotel 37.91113675706867 2017 8 City Hotel 36.04763437399421 2017 8 Resort Hotel 38.71508379888268

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_leadtime_stats AS
SELECT
  c.customer_type,
  -- median, 25th and 75th percentiles
  percentile_approx(f.lead_time, 0.5)        AS median_lead_time,
  percentile_approx(f.lead_time, 0.25)       AS p25_lead_time,
  percentile_approx(f.lead_time, 0.75)       AS p75_lead_time,
  AVG(f.lead_time)                          AS avg_lead_time
FROM fact_booking_partitioned f
JOIN dim_customer c
  ON f.customer_type_id = c.customer_type_id
GROUP BY c.customer_type
ORDER BY avg_lead_time DESC;

In [0]:
# Lead‐time stats by customer segment
lead_df = spark.table("vw_leadtime_stats")
display(lead_df)  

customer_type median_lead_time p25_lead_time p75_lead_time avg_lead_time Contract 114 28 261 143.34501480750248 Transient-Party 102 36 220 137.85659276073122 Transient 62 16 146 94.5213298095573 Group 12 1 43 45.72794117647059

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_holiday_cancel AS
SELECT
  h.hotel_type,
  case 
  when d.is_holiday = 1 then "Holiday"
  ELSE "Non-Holiday"
  END as is_holiday,
  AVG(f.is_canceled) * 100 AS cancel_rate_pct
FROM fact_booking_partitioned f
JOIN dim_date d      ON f.date_key = d.date_key
JOIN dim_hotel h     ON f.hotel_id = h.hotel_id
GROUP BY h.hotel_type, d.is_holiday
ORDER BY h.hotel_type, d.is_holiday;

In [0]:

# Holiday vs non‐holiday cancellation
hol_df = spark.table("vw_holiday_cancel")
display(hol_df)

hotel_type is_holiday cancel_rate_pct City Hotel Non-Holiday 42.01614934832474 City Hotel Holiday 47.53794890781192 Resort Hotel Non-Holiday 27.95066911571766 Resort Hotel Holiday 32.220367278797994

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_cancel_rate_daily AS
SELECT
  -- parse the ISO string into a Timestamp, then to a Date
  TO_DATE(
    TO_TIMESTAMP(
      d.date,
      "yyyy-MM-dd'T'HH:mm:ss.SSSXXX"
    )
  ) AS date,
  h.hotel_type,
  COUNT(*)                                      AS total_bookings,
  SUM(f.is_canceled)                            AS canceled_bookings,
  ROUND(SUM(f.is_canceled)*100.0/COUNT(*),2)     AS cancel_rate_pct
FROM fact_booking_partitioned f
JOIN dim_date d     ON f.date_key   = d.date_key
JOIN dim_hotel h    ON f.hotel_id = h.hotel_id
GROUP BY date, h.hotel_type
ORDER BY date, h.hotel_type;

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_cancel_rate_7d AS
SELECT
  date,
  hotel_type,
  cancel_rate_pct,
  ROUND(
    AVG(cancel_rate_pct) OVER (
      PARTITION BY hotel_type
      ORDER BY date
      ROWS BETWEEN 6 PRECEDING AND CURRENT ROW
    ),
    2
  ) AS rolling_7d_cancel_rate
FROM vw_cancel_rate_daily;

In [0]:
%sql
select * from vw_cancel_rate_7d

date hotel_type cancel_rate_pct rolling_7d_cancel_rate 2015-07-01 City Hotel 17.95 17.95 2015-07-02 City Hotel 97.96 57.96 2015-07-03 City Hotel 37.50 51.14 2015-07-04 City Hotel 76.32 57.43 2015-07-05 City Hotel 100.00 65.95 2015-07-06 City Hotel 96.67 71.07 2015-07-07 City Hotel 89.47 73.70 2015-07-08 City Hotel 42.11 77.15 2015-07-09 City Hotel 97.83 77.13 2015-07-10 City Hotel 77.78 82.88 2015-07-11 City Hotel 50.00 79.12 2015-07-12 City Hotel 100.00 79.12 2015-07-13 City Hotel 96.97 79.17 2015-07-14 City Hotel 100.00 80.67 2015-07-15 City Hotel 44.74 81.05 2015-07-16 City Hotel 100.00 81.36 2015-07-17 City Hotel 38.89 75.80 2015-07-18 City Hotel 62.96 77.65 2015-07-19 City Hotel 100.00 77.65 2015-07-20 City Hotel 96.61 77.60 2015-07-21 City Hotel 100.00 77.60 2015-07-22 City Hotel 77.78 82.32 2015-07-23 City Hotel 59.09 76.48 2015-07-24 City Hotel 100.00 85.21 2015-07-25 City Hotel 60.84 84.90 2015-07-26 City Hotel 100.00 84.90 2015-07-27 City Hotel 77.36 82.15 2015-07-28 City Hotel 33.33 72.63 2015-07-29 City Hotel 27.27 65.41 2015-07-30 City Hotel 93.88 70.38 2015-07-31 City Hotel 33.33 60.86 2015-08-01 City Hotel 54.29 59.92 2015-08-02 City Hotel 0.00 45.64 2015-08-03 City Hotel 85.22 46.76 2015-08-04 City Hotel 12.50 43.78 2015-08-05 City Hotel 47.93 46.74 2015-08-06 City Hotel 45.10 39.77 2015-08-07 City Hotel 50.00 42.15 2015-08-08 City Hotel 52.98 41.96 2015-08-09 City Hotel 7.14 42.98 2015-08-10 City Hotel 48.89 37.79 2015-08-11 City Hotel 9.84 37.41 2015-08-12 City Hotel 39.39 36.19 2015-08-13 City Hotel 65.22 39.07 2015-08-14 City Hotel 70.28 41.96 2015-08-15 City Hotel 55.65 42.34 2015-08-16 City Hotel 17.24 43.79 2015-08-17 City Hotel 51.91 44.22 2015-08-18 City Hotel 29.69 47.05 2015-08-19 City Hotel 2.70 41.81 2015-08-20 City Hotel 62.16 41.38 2015-08-21 City Hotel 17.50 33.84 2015-08-22 City Hotel 54.88 33.73 2015-08-23 City Hotel 8.70 32.51 2015-08-24 City Hotel 53.92 32.79 2015-08-25 City Hotel 52.81 36.10 2015-08-26 City Hotel 48.24 42.60 2015-08-27 City Hotel 77.59 44.81 2015-08-28 City Hotel 34.62 47.25 2015-08-29 City Hotel 21.43 42.47 2015-08-30 City Hotel 81.82 52.92 2015-08-31 City Hotel 37.18 50.53 2015-09-01 City Hotel 5.88 43.82 2015-09-02 City Hotel 11.36 38.55 2015-09-03 City Hotel 48.24 34.36 2015-09-04 City Hotel 18.12 32.00 2015-09-05 City Hotel 63.59 38.03 2015-09-06 City Hotel 10.99 27.91 2015-09-07 City Hotel 36.59 27.82 2015-09-08 City Hotel 34.67 31.94 2015-09-09 City Hotel 34.36 35.22 2015-09-10 City Hotel 69.23 38.22 2015-09-11 City Hotel 43.68 41.87 2015-09-12 City Hotel 56.67 40.88 2015-09-13 City Hotel 12.50 41.10 2015-09-14 City Hotel 29.59 40.10 2015-09-15 City Hotel 7.58 36.23 2015-09-16 City Hotel 39.09 36.91 2015-09-17 City Hotel 56.40 35.07 2015-09-18 City Hotel 63.75 37.94 2015-09-19 City Hotel 44.92 36.26 2015-09-20 City Hotel 35.71 39.58 2015-09-21 City Hotel 42.68 41.45 2015-09-22 City Hotel 11.25 41.97 2015-09-23 City Hotel 33.93 41.23 2015-09-24 City Hotel 61.96 42.03 2015-09-25 City Hotel 43.06 39.07 2015-09-26 City Hotel 59.50 41.16 2015-09-27 City Hotel 35.14 41.07 2015-09-28 City Hotel 51.61 42.35 2015-09-29 City Hotel 52.70 48.27 2015-09-30 City Hotel 60.53 52.07 2015-10-01 City Hotel 38.67 48.74 2015-10-02 City Hotel 10.18 44.05 2015-10-03 City Hotel 80.65 47.07 2015-10-04 City Hotel 25.23 45.65 2015-10-05 City Hotel 53.85 45.97 2015-10-06 City Hotel 45.53 44.95 2015-10-07 City Hotel 34.42 41.22 2015-10-08 City Hotel 54.55 43.49 2015-10-09 City Hotel 16.52 44.39 2015-10-10 City Hotel 55.36 40.78 2015-10-11 City Hotel 47.46 43.96 2015-10-12 City Hotel 32.81 40.95 2015-10-13 City Hotel 5.26 35.20 2015-10-14 City Hotel 9.68 31.66 2015-10-15 City Hotel 41.77 29.84 2015-10-16 City Hotel 65.19 36.79 2015-10-17 City Hotel 56.30 36.92 2015-10-18 City Hotel 16.92 32.56 2015-10-19 City Hotel 34.42 32.79 2015-10-20 City Hotel 14.10 34.05 2015-10-21 City Hotel 25.00 36.24 2015-10-22 City Hotel 17.07 32.71 2015-10-23 City Hotel 6.38 24.31 2015-10-24 City Hotel 58.54 24.63 201

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE TEMP VIEW vw_cancel_by_daytype_month AS
SELECT
  d.year,
  d.month,
  CASE WHEN d.is_weekend = 1 THEN 'Weekend' ELSE 'Weekday' END AS day_type,
  ROUND(AVG(f.is_canceled) * 100, 2) AS cancel_rate_pct
FROM fact_booking_partitioned f
JOIN dim_date d
  ON f.date_key = d.date_key
GROUP BY d.year, d.month, d.is_weekend
ORDER BY d.year, d.month, day_type;


In [0]:

cancel_wd_df = spark.table("vw_cancel_by_daytype_month")
display(cancel_wd_df)


year month day_type cancel_rate_pct 2015 7 Weekday 46.58 2015 7 Weekend 45.23 2015 8 Weekday 44.02 2015 8 Weekend 37.44 2015 9 Weekday 41.05 2015 9 Weekend 42.53 2015 10 Weekday 31.09 2015 10 Weekend 45.06 2015 11 Weekday 22.22 2015 11 Weekend 17.18 2015 12 Weekday 33.85 2015 12 Weekend 35.9 2016 1 Weekday 26.05 2016 1 Weekend 23.11 2016 2 Weekday 35.92 2016 2 Weekend 32.17 2016 3 Weekday 30.31 2016 3 Weekend 33.12 2016 4 Weekday 39.81 2016 4 Weekend 34.42 2016 5 Weekday 36.85 2016 5 Weekend 31.48 2016 6 Weekday 41.01 2016 6 Weekend 36.46 2016 7 Weekday 34.72 2016 7 Weekend 29.42 2016 8 Weekday 36.74 2016 8 Weekend 34.95 2016 9 Weekday 39.45 2016 9 Weekend 31.72 2016 10 Weekday 40.51 2016 10 Weekend 42.16 2016 11 Weekday 37.94 2016 11 Weekend 35.2 2016 12 Weekday 38.68 2016 12 Weekend 30.76 2017 1 Weekday 32.93 2017 1 Weekend 38.29 2017 2 Weekday 32.87 2017 2 Weekend 33.03 2017 3 Weekday 35.22 2017 3 Weekend 30.01 2017 4 Weekday 42.73 2017 4 Weekend 45.59 2017 5 Weekday 44.77 2017 5 Weekend 41.76 2017 6 Weekday 44.34 2017 6 Weekend 40.98 2017 7 Weekday 37.01 2017 7 Weekend 38.66 2017 8 Weekday 37.15 2017 8 Weekend 36.67

Databricks visualization. Run in Databricks to view.